In [7]:
import pandas as pd
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.utils import to_categorical
from tensorflow import keras as k
import tensorflow as tf

In [8]:
data = pd.read_csv("data/labeled.csv")
data = data.comment.str.lower()

In [9]:
tokenizer = Tokenizer()
tokenizer.fit_on_texts(data.values)
total_words = len(tokenizer.index_word)+1

In [10]:
input = []
for sequence in data.values:
    t_sequence = tokenizer.texts_to_sequences([sequence])[0]
    for i in range(1,len(t_sequence)):
        input.append(t_sequence[0:i+1])
input

[[16462, 9],
 [16462, 9, 15],
 [16462, 9, 15, 5],
 [16462, 9, 15, 5, 1367],
 [16462, 9, 15, 5, 1367, 6167],
 [279, 8],
 [279, 8, 27057],
 [279, 8, 27057, 27058],
 [279, 8, 27057, 27058, 27059],
 [279, 8, 27057, 27058, 27059, 1088],
 [279, 8, 27057, 27058, 27059, 1088, 978],
 [279, 8, 27057, 27058, 27059, 1088, 978, 6],
 [279, 8, 27057, 27058, 27059, 1088, 978, 6, 12],
 [279, 8, 27057, 27058, 27059, 1088, 978, 6, 12, 345],
 [279, 8, 27057, 27058, 27059, 1088, 978, 6, 12, 345, 55],
 [279, 8, 27057, 27058, 27059, 1088, 978, 6, 12, 345, 55, 355],
 [279, 8, 27057, 27058, 27059, 1088, 978, 6, 12, 345, 55, 355, 17],
 [279, 8, 27057, 27058, 27059, 1088, 978, 6, 12, 345, 55, 355, 17, 30],
 [279, 8, 27057, 27058, 27059, 1088, 978, 6, 12, 345, 55, 355, 17, 30, 345],
 [279, 8, 27057, 27058, 27059, 1088, 978, 6, 12, 345, 55, 355, 17, 30, 345, 3],
 [279,
  8,
  27057,
  27058,
  27059,
  1088,
  978,
  6,
  12,
  345,
  55,
  355,
  17,
  30,
  345,
  3,
  36],
 [279,
  8,
  27057,
  27058,
  27059,

In [11]:
len(input)

390090

In [12]:
input = pad_sequences(input, padding="pre")
input

array([[    0,     0,     0, ...,     0, 16462,     9],
       [    0,     0,     0, ..., 16462,     9,    15],
       [    0,     0,     0, ...,     9,    15,     5],
       ...,
       [    0,     0,     0, ...,    29,  6811,   159],
       [    0,     0,     0, ...,  6811,   159,  8271],
       [    0,     0,     0, ...,   159,  8271,   171]], dtype=int32)

In [13]:
with tf.device('/gpu:0'):
    model = k.Sequential([
        k.layers.Embedding(total_words,240, input_shape= (1036,)),
        k.layers.Bidirectional(k.layers.LSTM(150)),
        k.layers.Dense(68491, activation='softmax')
    ])

    model.compile(
        loss='categorical_crossentropy',
        metrics=['accuracy'],
        optimizer='Adam',
    )
    batch_size = 100

    for epoch in range(15):
        for i in range(0, len(input), batch_size):
            batch_input = input[i:i+batch_size, :-1]
            batch_labels = to_categorical(input[i:i+batch_size, -1], num_classes=68491)
            loss, accuracy = model.train_on_batch(batch_input, batch_labels)
            print(f"Epoch: {epoch+1}, Batch: {round(i/batch_size)}/{round(len(input)/batch_size)}, Loss: {loss}, Acc: {accuracy}")

2024-03-06 19:10:06.036944: I external/local_xla/xla/stream_executor/cuda/cuda_executor.cc:901] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero. See more at https://github.com/torvalds/linux/blob/v6.0/Documentation/ABI/testing/sysfs-bus-pci#L344-L355
2024-03-06 19:10:06.063840: I external/local_xla/xla/stream_executor/cuda/cuda_executor.cc:901] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero. See more at https://github.com/torvalds/linux/blob/v6.0/Documentation/ABI/testing/sysfs-bus-pci#L344-L355
2024-03-06 19:10:06.064006: I external/local_xla/xla/stream_executor/cuda/cuda_executor.cc:901] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero. See more at https://github.com/torvalds/linux/blob/v6.0/Documentation/ABI/testing/sysfs-bus-pci#L344-

Epoch: 1, Batch: 0/3901, Loss: 11.134432792663574, Acc: 0.0
Epoch: 1, Batch: 1/3901, Loss: 11.133230209350586, Acc: 0.029999999329447746
Epoch: 1, Batch: 2/3901, Loss: 11.131458282470703, Acc: 0.009999999776482582
Epoch: 1, Batch: 3/3901, Loss: 11.128066062927246, Acc: 0.05999999865889549
Epoch: 1, Batch: 4/3901, Loss: 11.122613906860352, Acc: 0.029999999329447746
Epoch: 1, Batch: 5/3901, Loss: 11.115501403808594, Acc: 0.0
Epoch: 1, Batch: 6/3901, Loss: 11.104853630065918, Acc: 0.05000000074505806
Epoch: 1, Batch: 7/3901, Loss: 11.080352783203125, Acc: 0.019999999552965164
Epoch: 1, Batch: 8/3901, Loss: 11.007533073425293, Acc: 0.05999999865889549
Epoch: 1, Batch: 9/3901, Loss: 10.903168678283691, Acc: 0.07999999821186066
Epoch: 1, Batch: 10/3901, Loss: 10.953001976013184, Acc: 0.0
Epoch: 1, Batch: 11/3901, Loss: 10.931553840637207, Acc: 0.009999999776482582
Epoch: 1, Batch: 12/3901, Loss: 10.774348258972168, Acc: 0.019999999552965164
Epoch: 1, Batch: 13/3901, Loss: 10.641095161437988,

In [44]:
model.save('toxic_t9.h5')

In [20]:
import pickle

with open('tokenizer.pickle', 'wb') as handle:
    pickle.dump(tokenizer, handle, protocol=pickle.HIGHEST_PROTOCOL)

CHECK

In [21]:
model = k.models.load_model('toxic_t9.h5')

In [43]:
import numpy as np

inputs = [
    "Ты просто пидор"
]
words_gen = 25

results = inputs.copy()  # Создаем копию списка входных строк

for i, seq in enumerate(inputs):
    for _ in range(words_gen):
        tokens = tokenizer.texts_to_sequences([seq])
        tokens = pad_sequences(tokens, maxlen=1036, padding="pre")
        predicted_probs = model.predict(tokens, verbose=0)
        predicted_class = np.argmax(predicted_probs)
        output_word = ""
        for word, index in tokenizer.word_index.items():
            if predicted_class == index:
                output_word = word
                break
        seq += "  " + output_word  # Обновляем входную последовательность
        results[i] = seq

print(results)



['Ты просто пидор  постящий  скримеры  и  считающий  это  смешным  борда  18  лет  большинство  сообщения  про  монополию  и  прочую  ебанину  я  в  россии  и  его  выебать  в  жопу  шпион']


['Тюбик  всё  всё  всё  всё  всё  всё  всё  всё  всё  всё']